In [0]:
%run "../includes/configuration"

In [0]:
from pyspark.sql.functions import col, sum, count, when
from pyspark.sql.functions import sum, when, col, count, desc, rank
from pyspark.sql.window import Window 

In [0]:
race_results = spark.read.parquet(f"{presentation_folder_path}/race_results")
display(race_results)

race_year race_name race_date circuit_location driver_name driver_number driver_nationality team fastest_lap race_time points position created_date 2014 Abu Dhabi Grand Prix 2014-11-23T13:00:00.000+0000 Abu Dhabi Lewis Hamilton 44 British Mercedes 49 1:39:02.619 50.0 1 2023-08-05T08:12:07.616+0000 2014 Abu Dhabi Grand Prix 2014-11-23T13:00:00.000+0000 Abu Dhabi Felipe Massa 19 Brazilian Williams 47 +2.576 36.0 2 2023-08-05T08:12:07.616+0000 2014 Abu Dhabi Grand Prix 2014-11-23T13:00:00.000+0000 Abu Dhabi Valtteri Bottas 77 Finnish Williams 54 +28.880 30.0 3 2023-08-05T08:12:07.616+0000 2019 Australian Grand Prix 2019-03-17T05:10:00.000+0000 Melbourne Valtteri Bottas 77 Finnish Mercedes 57 1:25:27.325 26.0 1 2023-08-05T08:12:07.616+0000 2019 Spanish Grand Prix 2019-05-12T13:10:00.000+0000 Montmeló Lewis Hamilton 44 British Mercedes 54 1:35:50.443 26.0 1 2023-08-05T08:12:07.616+0000 2019 Austrian Grand Prix 2019-06-30T13:10:00.000+0000 Spielburg Max Verstappen 33 Dutch Red Bull 60 1:22:01.822 26.0 1 2023-08-05T08:12:07.616+0000 2019 British Grand Prix 2019-07-14T13:10:00.000+0000 Silverstone Lewis Hamilton 44 British Mercedes 52 1:21:08.452 26.0 1 2023-08-05T08:12:07.616+0000 2019 German Grand Prix 2019-07-28T13:10:00.000+0000 Hockenheim Max Verstappen 33 Dutch Red Bull 61 1:44:31.275 26.0 1 2023-08-05T08:12:07.616+0000 2019 Russian Grand Prix 2019-09-29T11:10:00.000+0000 Sochi Lewis Hamilton 44 British Mercedes 51 1:33:38.992 26.0 1 2023-08-05T08:12:07.616+0000 2019 Abu Dhabi Grand Prix 2019-12-01T13:10:00.000+0000 Abu Dhabi Lewis Hamilton 44 British Mercedes 53 1:34:05.715 26.0 1 2023-08-05T08:12:07.616+0000 2020 Hungarian Grand Prix 2020-07-19T13:10:00.000+0000 Budapest Lewis Hamilton 44 British Mercedes 70 1:36:12.473 26.0 1 2023-08-05T08:12:07.616+0000 2020 Tuscan Grand Prix 2020-09-13T13:10:00.000+0000 Mugello Lewis Hamilton 44 British Mercedes 58 2:19:35.060 26.0 1 2023-08-05T08:12:07.616+0000 2020 Russian Grand Prix 2020-09-27T11:10:00.000+0000 Sochi Valtteri Bottas 77 Finnish Mercedes 51 1:34:00.364 26.0 1 2023-08-05T08:12:07.616+0000 2020 Portuguese Grand Prix 2020-10-25T12:10:00.000+0000 Portimão Lewis Hamilton 44 British Mercedes 63 1:29:56.828 26.0 1 2023-08-05T08:12:07.616+0000 2020 Emilia Romagna Grand Prix 2020-11-01T12:10:00.000+0000 Imola Lewis Hamilton 44 British Mercedes 63 1:28:32.430 26.0 1 2023-08-05T08:12:07.616+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Sebastian Vettel 5 German Ferrari 53 1:29:33.283 25.0 1 2023-08-05T08:12:07.616+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Sebastian Vettel 5 German Ferrari 21 1:32:01.940 25.0 1 2023-08-05T08:12:07.616+0000 2018 Chinese Grand Prix 2018-04-15T06:10:00.000+0000 Shanghai Daniel Ricciardo 3 Australian Red Bull 55 1:35:36.380 25.0 1 2023-08-05T08:12:07.616+0000 2018 Azerbaijan Grand Prix 2018-04-29T12:10:00.000+0000 Baku Lewis Hamilton 44 British Mercedes 35 1:43:44.291 25.0 1 2023-08-05T08:12:07.616+0000 2018 Spanish Grand Prix 2018-05-13T13:10:00.000+0000 Montmeló Lewis Hamilton 44 British Mercedes 64 1:35:29.972 25.0 1 2023-08-05T08:12:07.616+0000 2018 Monaco Grand Prix 2018-05-27T13:10:00.000+0000 Monte-Carlo Daniel Ricciardo 3 Australian Red Bull 13 1:42:54.807 25.0 1 2023-08-05T08:12:07.616+0000 2018 Canadian Grand Prix 2018-06-10T18:10:00.000+0000 Montreal Sebastian Vettel 5 German Ferrari 57 1:28:31.377 25.0 1 2023-08-05T08:12:07.616+0000 2018 French Grand Prix 2018-06-24T14:10:00.000+0000 Le Castellet Lewis Hamilton 44 British Mercedes 49 1:30:11.385 25.0 1 2023-08-05T08:12:07.616+0000 2018 Austrian Grand Prix 2018-07-01T13:10:00.000+0000 Spielburg Max Verstappen 33 Dutch Red Bull 70 1:21:56.024 25.0 1 2023-08-05T08:12:07.616+0000 2018 British Grand Prix 2018-07-08T13:10:00.000+0000 Silverstone Sebastian Vettel 5 German Ferrari 47 1:27:29.784 25.0 1 2023-08-05T08:12:07.616+0000 2018 German Grand Prix 2018-07-22T13:10:00.000+0000 Hockenheim Lewis Hamilton 44 British Mercedes 66 1:32:29.845 25.0 1 2023-

In [0]:
constructors = race_results.groupBy("team", "race_year") \
    .agg(
        sum(col("points")).alias("total_points"),
        count(when(col("position") == 1, True)).alias("Wins")
        )

display(constructors.filter("race_year = 2020"))

team race_year total_points Wins McLaren 2020 202.0 0 Williams 2020 0.0 0 Ferrari 2020 131.0 0 Racing Point 2020 210.0 1 Mercedes 2020 573.0 13 Red Bull 2020 319.0 2 AlphaTauri 2020 107.0 1 Renault 2020 181.0 0 Haas F1 Team 2020 3.0 0 Alfa Romeo 2020 8.0 0

In [0]:
constructor_rank_spec = Window.partitionBy("race_year").orderBy(desc("total_points"), desc("wins"))
final_df = constructors.withColumn("rank", rank().over(constructor_rank_spec))
display(final_df.filter("race_year = 2020"))

team race_year total_points Wins rank Mercedes 2020 573.0 13 1 Red Bull 2020 319.0 2 2 Racing Point 2020 210.0 1 3 McLaren 2020 202.0 0 4 Renault 2020 181.0 0 5 Ferrari 2020 131.0 0 6 AlphaTauri 2020 107.0 1 7 Alfa Romeo 2020 8.0 0 8 Haas F1 Team 2020 3.0 0 9 Williams 2020 0.0 0 10

In [0]:
constructors.write.mode("overwrite").parquet(f"{presentation_folder_path}/constructor_standings")